In [3]:
!pip install ray
!pip install redis

     -------------------------------------- 226.4/226.4 KB 7.0 MB/s eta 0:00:00


In [4]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
import json
import random
from BI_LSTM import LSTMTagger as LSTM
import os
from ray import tune
from ray.tune import CLIReporter
from ray.tune.schedulers import ASHAScheduler
import numpy as np
from functools import partial
import json
from sklearn.metrics import f1_score

torch.manual_seed(1)

AttributeError: partially initialized module 'ray' has no attribute '_private' (most likely due to a circular import)

In [5]:

def load_split_json(path, split:float = 0.8):

    file = open(path)

    data = json.load(file)

    test_labels = []
    train_labels = []
    for i in data.keys():
        val = random.uniform(0, 1)
        if val > split:
            test_labels.append(i)
        else:
            train_labels.append(i)


    train = []

    for label in train_labels:
        train.append(data[label])

    test_x = []
    test_y = []

    for label in test_labels:
        test_x.append(data[label][0])
        test_y.append(data[label][1])


    return train, test_x, test_y

In [6]:
def train_val_split(train_data:list, split = 0.8):

    val_subset = []
    train_subset = []
    for i in range(len(train_data)):
        val = random.uniform(0, 1)
        if val > split:
            val_subset.append(train_data[i])
        else:
            train_subset.append(train_data[i])

    return val_subset, train_subset


In [7]:
def train_cifar(config, checkpoint_dir=None, data_dir=None):

    tag_to_ix = {"idle": 0, "take-off": 1, "skill": 2, "landing": 3}


    # hidden_dim=config['hidden_dim']
    model = LSTM(embedding_dim=66, hidden_dim=4, num_layers=config['num_layers'], tagset_size=4 )

    loss_function = nn.NLLLoss()
    optimizer = optim.SGD(model.parameters(), lr=config['lr'], momentum=config['momentum'])
    if checkpoint_dir:
        model_state, optimizer_state = torch.load(
            os.path.join(checkpoint_dir, "checkpoint"))
        model.load_state_dict(model_state)
        optimizer.load_state_dict(optimizer_state)

    trainset, test_x, test_y = load_split_json(data_dir)

    val_subset, train_subset = train_val_split(trainset)

    for epoch in range(150):  # loop over the dataset multiple times
        running_loss = 0.0
        epoch_steps = 0

        for sentence, tags in train_subset:

            model.zero_grad()

            sentence_in = model.prepare_sequence_X(sentence)

            labels = model.prepare_sequence_Y(tags, tag_to_ix)
            tag_scores = model(sentence_in)

            loss = loss_function(tag_scores, labels)
            loss.backward()
            optimizer.step()

            running_loss += loss.item()
            epoch_steps += 1

            # if i % 2000 == 1999:  # print every 2000 mini-batches
            #     print("[%d, %5d] loss: %.3f" % (epoch + 1, i + 1,
            #                                     running_loss / epoch_steps))
            #     running_loss = 0.0


        # Validation loss
        val_loss = 0.0
        val_steps = 0
        total = 0
        correct = 0


        for sentence, tags in val_subset:

            with torch.no_grad():

                predicted = []

                sentence_in = model.prepare_sequence_X(sentence)

                labels = model.prepare_sequence_Y(tags, tag_to_ix)
                tag_scores = model(sentence_in)

                for frame in tag_scores:
                    frame_label = torch.argmax(frame)
                    predicted.append(int(frame_label))

                total += len(labels)
                correct += sum(list((map(lambda x, y: x == y, labels, predicted))))


                loss = loss_function(tag_scores, labels)
                val_loss += loss.cpu().numpy()
                val_steps += 1

        with tune.checkpoint_dir(epoch) as checkpoint_dir:
            path = os.path.join(checkpoint_dir, "checkpoint")
            torch.save((model.state_dict(), optimizer.state_dict()), path)

        tune.report(loss=(val_loss / val_steps), accuracy= correct / total)
    print("Finished Training")

In [8]:
def main(num_samples=10, max_num_epochs=50):
    data_dir = r'/Users/Morten/Library/CloudStorage/OneDrive-SharedLibraries-ITU/Sofus Sebastian Schou Konglevoll - Bachelor/all_skeleton/skeleton_from_csv.json'
    load_split_json(data_dir)
    config = {
        #"hidden_dim": tune.sample_from(lambda _: 2**np.random.randint(2, 7)),
        "num_layers": tune.choice([2,4,6,8]),
        "lr": tune.loguniform(1e-4, 1e-1),
        "momentum": tune.choice([0.1,0.2,0.3,0.4,0.5,0.6,0.7,0.8,0.9])
    }
    scheduler = ASHAScheduler(
        metric="loss",
        mode="min",
        max_t=max_num_epochs,
        grace_period=1,
        reduction_factor=2)
    reporter = CLIReporter(
        # parameter_columns=["l1", "l2", "lr", "batch_size"],
        metric_columns=["loss", "accuracy", "training_iteration"])
    result = tune.run(
        partial(train_cifar, data_dir=data_dir),
        config=config,
        num_samples=num_samples,
        scheduler=scheduler,
        progress_reporter=reporter)

    best_trial = result.get_best_trial("loss", "min", "last")
    print("Best trial config: {}".format(best_trial.config))
    print("Best trial final validation loss: {}".format(
        best_trial.last_result["loss"]))
    print("Best trial final validation accuracy: {}".format(
        best_trial.last_result["accuracy"]))


if __name__ == "__main__":
    # You can change the number of GPUs per trial here:
    main(num_samples=200, max_num_epochs=100)

2022-04-29 12:14:17,865	INFO logger.py:618 -- pip install "ray[tune]" to see TensorBoard files.
2022-04-29 12:14:17,866	WARNING callback.py:125 -- The TensorboardX logger cannot be instantiated because either TensorboardX or one of it's dependencies is not installed. Please make sure you have the latest version of TensorboardX installed: `pip install -U tensorboardx`
2022-04-29 12:14:18,186	INFO trial_runner.py:803 -- starting train_cifar_20fd5_00000
2022-04-29 12:14:20,955	INFO trial_runner.py:803 -- starting train_cifar_20fd5_00001
2022-04-29 12:14:20,974	INFO trial_runner.py:803 -- starting train_cifar_20fd5_00002
2022-04-29 12:14:21,005	INFO trial_runner.py:803 -- starting train_cifar_20fd5_00003


== Status ==
Current time: 2022-04-29 12:14:18 (running for 00:00:00.37)
Memory usage on this node: 10.1/16.0 GiB
Using AsyncHyperBand: num_stopped=0
Bracket: Iter 64.000: None | Iter 32.000: None | Iter 16.000: None | Iter 8.000: None | Iter 4.000: None | Iter 2.000: None | Iter 1.000: None
Resources requested: 1.0/4 CPUs, 0/0 GPUs, 0.0/5.46 GiB heap, 0.0/2.0 GiB objects
Result logdir: /Users/Morten/ray_results/train_cifar_2022-04-29_12-14-17
Number of trials: 16/200 (15 PENDING, 1 RUNNING)
+-------------------------+----------+-----------------+-------------+------------+--------------+
| Trial name              | status   | loc             |          lr |   momentum |   num_layers |
|-------------------------+----------+-----------------+-------------+------------+--------------|
| train_cifar_20fd5_00000 | RUNNING  | 127.0.0.1:58526 | 0.0813592   |        0.5 |            8 |
| train_cifar_20fd5_00001 | PENDING  |                 | 0.0248264   |        0.7 |            2 |
| train_

2022-04-29 12:14:56,798	INFO trial_runner.py:803 -- starting train_cifar_20fd5_00004


== Status ==
Current time: 2022-04-29 12:15:01 (running for 00:00:43.95)
Memory usage on this node: 10.6/16.0 GiB
Using AsyncHyperBand: num_stopped=1
Bracket: Iter 64.000: None | Iter 32.000: None | Iter 16.000: None | Iter 8.000: None | Iter 4.000: None | Iter 2.000: -0.8744817925126929 | Iter 1.000: -1.2547012187267224
Resources requested: 4.0/4 CPUs, 0/0 GPUs, 0.0/5.46 GiB heap, 0.0/2.0 GiB objects
Result logdir: /Users/Morten/ray_results/train_cifar_2022-04-29_12-14-17
Number of trials: 21/200 (16 PENDING, 4 RUNNING, 1 TERMINATED)
+-------------------------+------------+-----------------+-------------+------------+--------------+----------+------------+----------------------+
| Trial name              | status     | loc             |          lr |   momentum |   num_layers |     loss |   accuracy |   training_iteration |
|-------------------------+------------+-----------------+-------------+------------+--------------+----------+------------+----------------------|
| train_cifar_2

2022-04-29 12:15:18,363	INFO trial_runner.py:803 -- starting train_cifar_20fd5_00005


...

Result for train_cifar_20fd5_00194:
  accuracy: tensor(0.3608)
  date: 2022-04-29_13-31-51
  done: true
  experiment_id: 41ef6a155c1f4ddd87cb99c83e73d79d
  hostname: Macs-MacBook-Pro-2.local
  iterations_since_restore: 2
  loss: 1.3502285639444986
  node_ip: 127.0.0.1
  pid: 61170
  should_checkpoint: true
  time_since_restore: 69.21252202987671
  time_this_iter_s: 34.49885678291321
  time_total_s: 69.21252202987671
  timestamp: 1651231911
  timesteps_since_restore: 0
  training_iteration: 2
  trial_id: 20fd5_00194
  warmup_time: 0.004026889801025391
  
== Status ==
Current time: 2022-04-29 13:31:51 (running for 01:17:33.59)
Memory usage on this node: 8.7/16.0 GiB
Using AsyncHyperBand: num_stopped=196
Bracket: Iter 64.000: -0.3813647778960916 | Iter 32.000: -0.470021666753948 | Iter 16.000: -0.5636842286878685 | Iter 8.000: -0.7752176752758895 | Iter 4.000: -1.2321295529603957 | Iter 2.000: -1.3399259853363037 | Iter 1.000: -1.3617656364355213
Resources requested: 4.0/4 CPUs, 0/0 GPUs,

2022-04-29 13:31:53,783	INFO trial_runner.py:803 -- starting train_cifar_20fd5_00199


Result for train_cifar_20fd5_00195:
  accuracy: tensor(0.2278)
  date: 2022-04-29_13-31-57
  done: true
  experiment_id: 9db12e3b66474e0081e13499dd1cba51
  hostname: Macs-MacBook-Pro-2.local
  iterations_since_restore: 1
  loss: 1.3969678610563279
  node_ip: 127.0.0.1
  pid: 61187
  should_checkpoint: true
  time_since_restore: 35.16814422607422
  time_this_iter_s: 35.16814422607422
  time_total_s: 35.16814422607422
  timestamp: 1651231917
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: 20fd5_00195
  warmup_time: 0.004945039749145508
  
== Status ==
Current time: 2022-04-29 13:31:57 (running for 01:17:39.76)
Memory usage on this node: 8.8/16.0 GiB
Using AsyncHyperBand: num_stopped=197
Bracket: Iter 64.000: -0.3813647778960916 | Iter 32.000: -0.470021666753948 | Iter 16.000: -0.5636842286878685 | Iter 8.000: -0.7752176752758895 | Iter 4.000: -1.2321295529603957 | Iter 2.000: -1.3399259853363037 | Iter 1.000: -1.3618726765408236
Resources requested: 4.0/4 CPUs, 0/0 GPUs,

2022-04-29 13:34:05,014	INFO tune.py:701 -- Total run time: 4787.17 seconds (4786.94 seconds for the tuning loop).


Best trial config: {'num_layers': 2, 'lr': 0.09508944332753301, 'momentum': 0.7}
Best trial final validation loss: 0.3980354515737609
Best trial final validation accuracy: 0.8407439589500427


In [ ]:
lt =[1,4,2,5]
tl = [1,4,5,2]

p = sum(list((map(lambda x, y: x == y, lt, tl))))

In [50]:
p

2